In [1]:
import requests
import os
import csv
import json
import pandas as pd
import folium
from IPython.display import display

# Define your access token and sequence ID
access_token = 'MLY|8196090173836012|99bcaed29312ec0d1c06b22447943d94'
header = {'Authorization' : 'OAuth {}'.format(access_token)}
metadata_endpoint = "https://graph.mapillary.com"


def getSequence(sequence_id, access_token=access_token, headers=header):
    url = "https://graph.mapillary.com/image_ids?sequence_id={}".format(sequence_id)
    r = requests.get(url, headers=header)
    data_sequence = r.json()
    print("Number of Images found in Sequence: " + str(len(data_sequence['data'])))
    return data_sequence



def getBoundingBoxImages(testpoint, x_dist, y_dist, access_token=access_token , headers=header):
    # Construct the image search URL with the bounding box
    url_imagesearch = metadata_endpoint + '/images?fields=id,location&bbox={}, {}, {}, {}'.format(
        testpoint[1] - x_dist, testpoint[0] - y_dist,
        testpoint[1] + x_dist, testpoint[0] + y_dist
    )
    # Request to search for images
    response_imagesearch = requests.get(url_imagesearch, headers=headers)
    data_imagesearch = response_imagesearch.json()
    print("Number of Images found in bounding box: " + str(len(data_imagesearch['data'])))
    return data_imagesearch

def getImage(image_id, access_token=access_token, headers=header):
    url = "https://graph.mapillary.com/:image_ids={}".format(image_id)
    r = requests.get(url, headers=header)
    data_sequence = r.json()
    print(data_sequence)
    #print("Number of Images found in Sequence: " + str(len(data_sequence['data'])))
    return data_sequence



# Define bounding box center and distances to get an area to download from 
x_dist = 0.050
y_dist = 0.050
testpoint = [52.0881575, 5.1143055]  # Example: Center point
zod_sequence_000002 = [52.204000594370456,9.937544328537447]

def saveImages(folder_name, data, headers=header):
    metadata_endpoint = "https://graph.mapillary.com"

    if 'data' in data:
        # Create a directory to save images if it doesn't exist
        os.makedirs(str(folder_name), exist_ok=True)
        csv_file_path = str(folder_name)+'/metadata.csv'
        with open(csv_file_path, mode='w', newline='') as csv_file:
            fieldnames = ['id', 'thumb_2048_url', 'captured_at', 'sequence', 'lat', 'long', 'orientation','rotation','f', 'k1', 'k2', 'sfm_lat', 'sfm_long']
            writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
            writer.writeheader()

            for image in data['data']:
                # Fetch detailed information for each image
                url_image = metadata_endpoint + '/{}?fields=id,thumb_2048_url,captured_at,sequence,geometry,compass_angle,computed_rotation,camera_parameters,computed_geometry'.format(image['id'])
                response_image = requests.get(url_image, headers=headers)
                data_image = response_image.json()

                # Print image data (for debugging)
                #print(data_image)

                # Extract information
                img_id = data_image.get('id')
                img_url = data_image.get('thumb_2048_url')
                captured_at = data_image.get('captured_at')
                sequence = data_image.get('sequence')
                location = data_image.get('geometry')
                sfm_location = data_image.get('computed_geometry')
                orientation = data_image.get('compass_angle')
                rotation = data_image.get('computed_rotation')
                camera_params = data_image.get('camera_parameters')

                # Extract coordinates and orientation
                if location:
                    coordinates = location.get('coordinates')
                    print("coordinates",coordinates)
                    if coordinates:
                        longitude = coordinates[0]
                        latitude = coordinates[1]
                    else:
                        longitude = None
                        latitude = None
                else:
                    longitude = None
                    latitude = None

                #extract sfm location    
                if sfm_location:
                    print("sfm_location: ",sfm_location)
                    sfm_coordinates = sfm_location.get('coordinates')
                    if coordinates:
                        sfm_longitude = sfm_coordinates[0]
                        sfm_latitude = sfm_coordinates[1]
                    else:
                        sfm_longitude = None
                        sfm_latitude = None
                else:
                    sfm_longitude = None
                    sfm_latitude = None

                
                #extract intrinsics
                if camera_params:
                    focal_length = camera_params[0]
                    k1 = camera_params[1]
                    k2 = camera_params[2]
                else: 
                    focal_length = None
                    k1 = None
                    k2 = None


                

                # Save image metadata to CSV
                writer.writerow({
                    'id': img_id,
                    'thumb_2048_url': img_url,
                    'captured_at': captured_at,
                    'sequence': sequence,
                    'lat': latitude,
                    'long': longitude,
                    'orientation': orientation,
                    'rotation': rotation,
                    'f': focal_length,
                    'k1': k1,
                    'k2': k2,
                    'sfm_lat': sfm_latitude,
                    'sfm_long': sfm_longitude
                })

                # Download the image and save it to the local directory
                if img_url:
                    img_response = requests.get(img_url)
                    if img_response.status_code == 200:
                        img_filename = f'{folder_name}/{img_id}.jpg'
                        with open(img_filename, 'wb') as f:
                            f.write(img_response.content)
                        print(f'Downloaded {img_id}.jpg')
                    else:
                        print(f'Failed to download image {img_id}.jpg')
                else:
                    print(f'No URL found for image {img_id}')
    else:
        print(f"No images found for sequence.")



def csvPlot(csv_file_path):
    metadata = pd.read_csv(csv_file_path)
    # Create a map centered at the average coordinates
    avg_latitude = metadata['lat'].mean()
    avg_longitude = metadata['long'].mean()
    map_center = [avg_latitude, avg_longitude]

    # Initialize the map
    mymap = folium.Map(location=map_center, zoom_start=15)

    # Add markers for each image's GPS location with orientation
    for index, row in metadata.iterrows():
        lat = row['lat']
        long = row['long']
        img_id = row['id']
        img_url = row['thumb_2048_url']
        angle = row['orientation']  # Assuming this is the compass angle
        
        # Circle with a bold arrow inside, rotating the arrow based on the angle
        icon_html = f"""
        <div style="
            position: relative;
            width: 30px;
            height: 30px;
            border-radius: 50%;
            background-color: blue;
            border: 1px solid white;
            text-align: center;
            line-height: 30px;
            ">
            <div style="
                transform: rotate({angle}deg);
                position: absolute;
                top: 50%;
                left: 50%;
                transform-origin: center;
                font-size: 20px;  /* Increased font size */
                font-weight: bold; /* Makes the arrow appear bolder */
                color: black;
                ">
                &#x21E7;  <!-- Thicker arrow character -->
            </div>
        </div>
        """

        # Add the marker with the custom circle + bold arrow icon
        folium.Marker(
            location=[lat, long],
            popup=f'<img src="{img_url}" width="200"><br>ID: {img_id}',
            icon=folium.DivIcon(html=icon_html)
        ).add_to(mymap)

    # Display the map in the Jupyter Notebook
    display(mymap)











In [3]:

# csv_file_path = 'mapillary_sequence_with_intrinsics/metadata.csv'
# sequence_2 = 'thCfqXmxKGITujoiksp73L'
# data_sequence=getSequence(sequence_2)
# saveImages('mapillary_sequence_with_intrinsics', data_sequence)


csv_file_zod = '/home/bjangley/VPR/mapillary_utils/zod_000002/metadata.csv'
data_sequence = getBoundingBoxImages(zod_sequence_000002, x_dist, y_dist)
saveImages('zod_000002', data_sequence)

Number of Images found in bounding box: 2000
coordinates [9.9367268445305, 52.169467154467]
sfm_location:  {'type': 'Point', 'coordinates': [9.9367722242878, 52.169485584223]}
Downloaded 1374021562958983.jpg
coordinates [9.964313, 52.1867233]
sfm_location:  {'type': 'Point', 'coordinates': [9.9643559414894, 52.18673845163]}
Downloaded 1548992319165739.jpg
coordinates [9.9844088, 52.1973068]
sfm_location:  {'type': 'Point', 'coordinates': [9.9844088, 52.1973068]}
Downloaded 1830370247400610.jpg
coordinates [9.9445809999188, 52.250953]
sfm_location:  {'type': 'Point', 'coordinates': [9.9445809957747, 52.250952999787]}
Downloaded 1985534538287846.jpg
coordinates [9.9680083299975, 52.164136110004]
sfm_location:  {'type': 'Point', 'coordinates': [9.9680080124773, 52.164136036069]}
Downloaded 2946483592237931.jpg
coordinates [9.944481327014, 52.197799872898]
sfm_location:  {'type': 'Point', 'coordinates': [9.9445164799281, 52.197786274609]}
Downloaded 1434280856926120.jpg
coordinates [9.9277

In [9]:
# Load the metadata from the CSV file
csv_file_path = 'mapillary_sequence_3/metadata.csv'
sequence_2 = 'Hq1toy7ABF2wU6S4zxbeXJ'
data_sequence=getSequence(sequence_2)
saveImages('mapillary_sequence_3', data_sequence)

Number of Images found in Sequence: 263
coordinates [5.1217515, 52.090686]
sfm_location:  {'type': 'Point', 'coordinates': [5.1218169950448, 52.090660997087]}
Downloaded 1240164577396442.jpg
coordinates [5.1217149, 52.0906678]
sfm_location:  {'type': 'Point', 'coordinates': [5.1217943942541, 52.090653203481]}
Downloaded 2855724447917305.jpg
coordinates [5.1217191, 52.0906764]
sfm_location:  {'type': 'Point', 'coordinates': [5.1217358847475, 52.090680115608]}
Downloaded 458384550402570.jpg
coordinates [5.1216788, 52.0906998]
sfm_location:  {'type': 'Point', 'coordinates': [5.1216441219492, 52.090757245202]}
Downloaded 868605348464322.jpg
coordinates [5.1216594, 52.0907388]
sfm_location:  {'type': 'Point', 'coordinates': [5.1216252022311, 52.090782518782]}
Downloaded 1180874919618555.jpg
coordinates [5.1216556, 52.0907736]
sfm_location:  {'type': 'Point', 'coordinates': [5.1216253428435, 52.090806074375]}
Downloaded 507135708517432.jpg
coordinates [5.1216635, 52.0908119]
sfm_location:  {

In [13]:
# image_id = '799338198457726'
# image_sequence=getImage(799338198457726)
# csv_file_utrecht='/home/bjangley/VPR/mast3r/datasets/utrecht/metadata.csv'
# utrecht_customdataset = '/home/bjangley/VPR/mast3r/datasets/utrecht/'
# saveImages(utrecht_customdataset,image_sequence)

{'error': {'message': "Unsupported get request. Object with ID ':image_ids=799338198457726' does not exist, cannot be loaded due to missing permissions, or does not support this operation", 'type': 'MLYApiException', 'code': 100, 'error_subcode': 33, 'fbtrace_id': 'AsFQyQj_qCzoIHlYKv9XKTb'}}
No images found for sequence.


In [4]:
csvPlot(csv_file_zod)